In [1]:
import pandas as pd
import os
import matplotlib.pyplot as plt
import squarify
from dotenv import load_dotenv

# 한글 폰트 설정
plt.rcParams['font.family'] = 'Malgun Gothic'
plt.rcParams['axes.unicode_minus'] = False

# .env 파일 로드
load_dotenv()

# 환경변수에서 파일 경로 가져오기
file_path1 = r'E:\machin-prj\review_data_seoul_incheon_final.csv' # 리뷰 서울인천 전체
file_path2 =r'E:\machin-prj\ZB)TourAPI_area_based_seoul_incheon_FINAL.xlsx'   # 지역코드 전체

In [2]:
# ✅ 데이터 불러오기
df_review = pd.read_csv(file_path1)   # 경기·인천
df_area = pd.read_excel(file_path2)  # 서울

In [3]:

merged_df = pd.merge(
    df_review,
    df_area[['contentid', 'cat1', 'cat2', 'cat3', 'mapx', 'mapy']],
    on='contentid',
    how='left'
)

merged_df.head(1)

검색어     장소명    평점                주소 리뷰닉네임   별점           날짜 리뷰내용  \
0  갈현체육공원  갈현체육공원  5.0점  인천광역시 계양구 황어로 66     .  5.0  2022.06.07.  NaN   

    title                   addr1  contentid  contenttypeid cat1   cat2  \
0  갈현체육공원  인천광역시 계양구 황어로 66 (갈현동)    3061205             12  A02  A0202   

        cat3        mapx       mapy  
0  A02020700  126.728577  37.577721

In [4]:
# 1. merged_data를 복사하고, 필요한 컬럼명 재정의 (소분류항목, 주소)
#    여기서는 cat3를 소분류항목으로, addr1을 주소로 사용합니다.
df = merged_df.copy()
df = df.rename(columns={'addr1': '상세주소', 'cat1': '대분류항목'})


# 2. 리뷰의 여러 컬럼을 하나의 문자열로 합쳐서 "리뷰데이터" 컬럼 생성
#    (여기서는 '검색어', '장소명', '평점', '리뷰닉네임', '별점', '날짜', '리뷰내용' 컬럼을 합칩니다)
df['리뷰데이터'] = df[['검색어', '장소명', '평점', '리뷰닉네임', '별점', '날짜', '리뷰내용']]\
    .apply(lambda row: ', '.join(row.dropna().astype(str)), axis=1)

# 3. (그룹화) 소분류항목, 주소, mapx, mapy를 기준으로 리뷰데이터를 리스트로 묶습니다.
grouped = df.groupby(['대분류항목', '주소', 'mapx', 'mapy'])['리뷰데이터'].apply(list).reset_index()

# 4. 각 그룹에서 첫 번째, 두 번째 리뷰를 새로운 컬럼으로 분리
def extract_reviews(review_list):
    review1 = review_list[0] if len(review_list) > 0 else ''
    review2 = review_list[1] if len(review_list) > 1 else ''
    return pd.Series([review1, review2], index=['리뷰데이터1', '리뷰데이터2'])

review_data_cols = grouped['리뷰데이터'].apply(extract_reviews)

# 5. 최종 결과 데이터프레임 구성
result_df = pd.concat([grouped.drop(columns=['리뷰데이터']), review_data_cols], axis=1)

# 결과 출력: 소분류항목, 주소, mapx, mapy, 리뷰데이터1, 리뷰데이터2
result_df

대분류항목                               주소        mapx       mapy  \
0      A01              서울특별시 강남구 대치동 78-25  127.103617  37.493129   
1      A01               서울특별시 강남구 삼성동 79-1  117.992566  19.694427   
2      A01              서울특별시 강남구 신사동 649-9  127.033812  37.521463   
3      A01              서울특별시 강남구 일원동 53-22  127.075090  37.477586   
4      A01              서울특별시 강남구 일원동 732-3  127.078398  37.480477   
...    ...                              ...         ...        ...   
4991   A05            인천광역시 중구 홍예문로 12 1-3층  126.624073  37.471834   
4992   A05            인천광역시 중구 홍예문로 13 1,2층  126.623525  37.471962   
4993   A05             인천광역시 중구 홍예문로68번길 28  126.628628  37.475817   
4994   A05          인천광역시 중구 홍예문로68번길 29 1층  126.628605  37.476042   
4995   A05  인천광역시 중구 화랑목로 50-10 1층 101~103호  126.498950  37.496348   

                                                 리뷰데이터1  \
0     탄천, 탄천공영주차장, 3.3점, cxncnrienf288r, 1.0, 2025.0...   
1         삼성해맞이공원, 삼성해맞이공원, 4.9점, 황진성, 5.0, 2025.03.27.   
2          도산공원, 도산근린공원, 4.6점, M, 5.0, 2025.02.18., 굿굿    
3     대모산도시자연공원, 대모산도시자연공원, 4.5점, 사랑스러운 유경이, 5.0, 20...   
4     대모산숲속야생화원, 대모산숲속야생화원, 4.7점, Seo heonhee, 5.0, ...   
...                                                 ...   
4991  중화루, 중화루, 3.6점, 밤우유, 5.0, 2025.04.08., 인생 맛집 그...   
4992                                 최고집 신포본점, 최고집 신포본점   
4993          양산박삼치, 양산박삼치, 3.3점, 이나가, 3.0, 2024.09.22.   
4994  전동삼치, 전동삼치, 3.9점, xi자이자식아, 1.0, 2025.01.25., 정...   
4995                                      닭곰탱이 본점, 닭곰탱이   

                                                 리뷰데이터2  
0     탄천, 탄천공영주차장, 3.3점, Dohyun Lee, 5.0, 2024.01.23...  
1     삼성해맞이공원, 삼성해맞이공원, 4.9점, Dane(별점은후함,후기는솔직), 5.0...  
2         도산공원, 도산근린공원, 4.6점, 삼성동블루베리, 5.0, 2025.01.15.  
3     대모산도시자연공원, 대모산도시자연공원, 4.5점, 🇰🇷, 5.0, 2023.04.1...  
4     대모산숲속야생화원, 대모산숲속야생화원, 4.7점, 백명석, 5.0, 2021.09.05.  
...                                                 ...  
4991  중화루, 중화루, 3.6점, 비오는날, 4.0, 2025.03.28., 아주 조금 ...  
4992                                                     
4993  양산박삼치, 양산박삼치, 3.3점, Thomas, 5.0, 2023.09.10., ...  
4994          전동삼치, 전동삼치, 3.9점, 정연구40, 5.0, 2024.10.22.  
4995                                                     

[4996 rows x 6 columns]

In [5]:
# 1. 소분류항목별 행의 개수를 계산합니다.
group_counts = result_df.groupby("대분류항목").size().reset_index(name="count")

# 2. 개수 기준 내림차순으로 정렬한 후, 상위 30개의 소분류항목을 선택합니다.
top30_categories = group_counts.sort_values("count", ascending=False).head(30)["대분류항목"].tolist()

# 3. result_df에서 top30_categories에 해당하는 소분류항목의 행만 필터링합니다.
top30 = result_df[result_df["대분류항목"].isin(top30_categories)]


In [6]:
import folium

# 1. 지도 중심 좌표 계산 (여기서는 각 데이터의 평균 좌표 사용)
center_lat = top30['mapy'].mean()
center_lon = top30['mapx'].mean()

# 2. folium Map 객체 생성 (위치: [center_lat, center_lon])
my_map = folium.Map(location=[center_lat, center_lon], zoom_start=12)

# 3. 각 행의 데이터에 대해 마커 추가 (folium.Marker)
for idx, row in top30.iterrows():
    # folium은 [위도, 경도] 순서로 좌표 지정해야 합니다.
    latitude = row['mapy']
    longitude = row['mapx']
    
    # 팝업에 표시할 내용: 예시에서는 주소, 소분류항목, 첫 번째 리뷰 데이터를 포함합니다.
    popup_text = (f"<b>주소:</b> {row['주소']}<br>"
                  f"<b>대분류항목:</b> {row['대분류항목']}<br>"
                  f"<b>리뷰데이터1:</b> {row['리뷰데이터1'][:100]}...")  # 너무 긴 경우 일부만 표시
    
    folium.Marker(location=[latitude, longitude],
                  popup=folium.Popup(popup_text, max_width=300),
                  tooltip=row['대분류항목']).add_to(my_map)

# 4. 지도를 HTML 파일로 저장하거나, 노트북 환경이라면 바로 출력할 수 있습니다.
my_map.save("map_visualization.html")
my_map
